# Notebook 04bis - Fit results exploitation and plot formatting

This notebook covers plotting and exporting figures from fit results

In [1]:
%matplotlib qt
%config Completer.use_jedi = False
import hyperspy.api as hs
import numpy as np
import matplotlib.pyplot as plt

# from hyperspy.axes import FunctionalDataAxis
from matplotlib.colors import DivergingNorm
from matplotlib import cm

#Needed to export the pdf
from matplotlib.backends.backend_pdf import PdfPages
import matplotlib
matplotlib.rcParams['pdf.fonttype'] = 42

C:\Users\NicolasTappy\Miniconda3\envs\hs_dev\lib\site-packages\pyUSID\viz\__init__.py:18: FutureWarning: Please use sidpy.viz.plot_utils instead of pyUSID.viz.plot_utils. pyUSID.plot_utils will be removed in a future release of pyUSID
  FutureWarning)


### Loading

In [2]:
clmap_ev = hs.load('clmap_IIB-HPHT-diamond_eV_with_model.hspy')

In [3]:
clmap_ev.models

└── Diamond_7_peaks
    ├── components
    │   ├── BXLO
    │   ├── BXNP
    │   ├── BXTO
    │   ├── BXTO_O
    │   ├── FXTA
    │   ├── FXTO
    │   └── FXTO_O
    ├── date = 2021-10-25 12:04:26
    └── dimensions = (63, 64|875)

In [4]:
mod = clmap_ev.models.restore('Diamond_7_peaks')

### Plotting everything in an orderly fashion

Parameter maps typically need some re-factoring after the fit has been done. Example: FWHM of a peak is typically more intuitively represented in meV than eV. Here we create a large dictionnary with all parameter maps for all components in the model, both standard deviation and values

In [5]:
parameter_maps_dictionary = {}
for i in mod:
    sig_dic = {}
    for parameter in i.parameters:
        sig_dic[parameter.name] = {}
        
        #Formatting for values
        k = 'values'

        tmp = parameter.as_signal(field=k).deepcopy()
        
        if parameter.name=='A':
            unit = '[au]'
            tmp.metadata.Signal.quantity='I'+unit
        elif parameter.name=='centre':
            unit = '[eV]'
            tmp.metadata.Signal.quantity='Energy [eV]'
        elif parameter.name=='gamma':
            unit = '[meV]'
            tmp.metadata.Signal.quantity='Energy [meV]'
            tmp.data *= 1000
        
        tmp.metadata.General.title =  " ".join([parameter.name,unit])
        sig_dic[parameter.name][k] = tmp
        
        k = 'std'
        tmp = parameter.as_signal(field=k).deepcopy()
    
        if parameter.name=='A':
            unit = '[%]'
            tmp.metadata.Signal.quantity='I'+unit
            tmp.data = (tmp.data/parameter.map['values'])*100
        elif parameter.name=='centre':
            unit = '[meV]'
            tmp.metadata.Signal.quantity='Energy'+unit
            tmp.data *= 1000
        elif parameter.name=='gamma':
            unit = '[meV]'
            tmp.metadata.Signal.quantity='Energy'+unit
            tmp.data *= 1000

        tmp.metadata.General.title =  " ".join([parameter.name,k,unit])
        sig_dic[parameter.name][k] = tmp
    
    parameter_maps_dictionary[i.name] = sig_dic

In the data structure, all parameter maps are available as hyperspy signals multi nested in dictionary
Example: getting the hyperspy signal of peak area parameter of the BXTO peak, or std

In [6]:
parameter_maps_dictionary['BXTO']['A']['values']

<Signal2D, title: A [au], dimensions: (|63, 64)>

In [7]:
parameter_maps_dictionary['BXTO']['A']['std']

<Signal2D, title: A std [%], dimensions: (|63, 64)>

We initialise color maps for plotting parameter maps in a standard way 

In [8]:
#A fit value map
c1 = cm.get_cmap('Spectral_r') #We use a map from the matplotlib library
c1.set_bad([0.6,0.6,0.6])      #the set_bad method from color maps allows                               
#A fit std map                 #to give a definite color to non measured points
c2 = cm.get_cmap('plasma')     #Note that plasma is the chosen color map for all std maps
c2.set_bad([0.6,0.6,0.6])

#gamma fit value map
c3 = cm.get_cmap('PiYG')
c3.set_bad([0.6,0.6,0.6])
#gamma fit std map
c4 = cm.get_cmap('plasma')
c4.set_bad([0.6,0.6,0.6])

#centre fit value map
c5 = cm.get_cmap('RdYlGn')
c5.set_bad([0.6,0.6,0.6])
#centre fit std map
c6 = cm.get_cmap('plasma')
c6.set_bad([0.6,0.6,0.6])

coldic = {"A_val":c1,
          "A_std":c2,
          "gamma_val":c3,
          "gamma_std":c4,
          "centre_val":c5,
          "centre_std":c6,
          }

In [9]:
#Plot of all components in the fit.

#For each component
for key,val in parameter_maps_dictionary.items():
    #list of figures
    list_figs = [j for i in val.values() for j in i.values()]
    
    #create a figure
    fig = plt.figure(figsize=(90/25.4,120/25.4))
    
    #plot all parameters values and std maps
    hs.plot.plot_images(list_figs,
                        cmap=coldic.values(),
                        no_nans=False,
                        per_row=2,
                        label='auto',
                        labelwrap=30,
                        suptitle=key,
                        suptitle_fontsize=14,
                        colorbar='multi',
                        centre_colormap=False,
                        scalebar=[0],
                        scalebar_color='black',
                        axes_decor='off',
                        padding=None,
                        tight_layout=True,
                        aspect='auto',
                        min_asp=0.1,
                        namefrac_thresh=0.1,
                        fig=fig,
                        vmin="1th",
                        vmax="99th",)
    
    fig.subplots_adjust(top=0.9)
    
    #save as pdf if wanted
#     with PdfPages(key+'.pdf') as pdf:    
#         pdf.savefig()

In [10]:
plt.close('all')

### Chi-squared map

When plotting reduced Chi-squared, it is useful to know if the value is larger or smaller than 1. 

A good way to present this in a intuitive way is to plot $\chi^2 - 1$ and use one of matplotlib diverging color maps, that use a neutral color at 0:

https://matplotlib.org/stable/tutorials/colors/colormaps.html

In [11]:
#Object Creation
rcs = mod.red_chisq.deepcopy()
rcs.metadata.Signal.quantity = "$\chi^2_{red}$"

#Color map customisation
rcs_cmap = cm.BrBG_r
rcs_cmap.set_bad([0.6,0.6,0.6])

In [13]:
hs.plot.plot_images(rcs,
                    cmap=rcs_cmap,
                    norm=DivergingNorm(vcenter=1.0,vmin=0.0,vmax=2.0),
                    vmin=0.0,
                    vmax=2.0,
                    centre_colormap=False,
                    axes_decor='off',
                    scalebar='all',
                    scalebar_color='black',
                    )


#Adjust fig size
f = plt.gcf()
f.set_size_inches((80/25.4,60/25.4))
plt.suptitle('')

#Remove scalebar text if you want
sbt = f.get_children()[1].get_children()[1]
sbt.set_text('')

cbar = f.get_children()[1].images[-1].colorbar
cbar.set_ticks([0.0,0.5,1.0,1.5,2.0])
cbar.set_label("$\chi^2_{red}$")

#Apply tight layout
plt.tight_layout()

#save
# with PdfPages('reduced_chi_squared_map_with_variance.pdf') as pdf:    
#     pdf.savefig()

To compute the reduced chi square statistics

In [14]:
from scipy.stats import chi2

Computing fit degree of freedom. Be careful! In hyperspy the degrees of freedom mean the number of parameters allowed to vary in the model which is not the same. In fit results analysis it is the number of fit datapoints - number of parameters

In [15]:
fit_dof = mod.channel_switches.sum() - mod.dof.data.max()
fit_dof

240

In [16]:
#Chi squared statistics
mean, var, skew, kurt = chi2.stats(fit_dof, moments='mvsk')

#Reduced chi square statistics, i.e. chi-squared per degree of freedom
#Three sigma interval. The fit results can be questionable for reduced chi square above this value
three_sig_chisq_val = mean/fit_dof+3*(var**0.5/fit_dof)

three_sig_chisq_val

1.2738612787525831